In [ ]:
#  https://github.com/veeps/shelter_status

In [75]:
import datetime as dt
import pandas as pd
import re
import numpy as np
import nltk
import regex as reg
import matplotlib.pyplot as plt

from twitterscraper import query_tweets
from sklearn.decomposition import LatentDirichletAllocation as LDA
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import RegexpTokenizer
from nltk.stem.porter import PorterStemmer
from nltk.corpus import stopwords
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.feature_extraction import stop_words
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
from sklearn.datasets import make_multilabel_classification
from bs4 import BeautifulSoup



pd.set_option('display.max_columns', 500)

## KINCADE FIRE

In [2]:
lang= 'english'
kincade_begin_date = dt.date(2019,10,23)
kincade_end_date = dt.date(2019,11,15)
limit = 30000

In [4]:
tweets_kincade = query_tweets('kincadefire', begindate=kincade_begin_date, kincade_end_date=end_date,
                     limit=limit, lang=lang)  # October 23 - November 15, 2019

INFO: queries: ['kincadefire since:2019-10-23 until:2019-10-24', 'kincadefire since:2019-10-24 until:2019-10-25', 'kincadefire since:2019-10-25 until:2019-10-26', 'kincadefire since:2019-10-26 until:2019-10-27', 'kincadefire since:2019-10-27 until:2019-10-28', 'kincadefire since:2019-10-28 until:2019-10-29', 'kincadefire since:2019-10-29 until:2019-10-31', 'kincadefire since:2019-10-31 until:2019-11-01', 'kincadefire since:2019-11-01 until:2019-11-02', 'kincadefire since:2019-11-02 until:2019-11-03', 'kincadefire since:2019-11-03 until:2019-11-04', 'kincadefire since:2019-11-04 until:2019-11-05', 'kincadefire since:2019-11-05 until:2019-11-06', 'kincadefire since:2019-11-06 until:2019-11-08', 'kincadefire since:2019-11-08 until:2019-11-09', 'kincadefire since:2019-11-09 until:2019-11-10', 'kincadefire since:2019-11-10 until:2019-11-11', 'kincadefire since:2019-11-11 until:2019-11-12', 'kincadefire since:2019-11-12 until:2019-11-13', 'kincadefire since:2019-11-13 until:2019-11-15']
INFO

INFO: Using proxy 12.218.209.130:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1193940276743745542-1194032896010358784&q=kincadefire%20since%3A2019-11-11%20until%3A2019-11-12&l=english
INFO: Using proxy 12.218.209.130:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1194302253626253313-1194395000769011712&q=kincadefire%20since%3A2019-11-12%20until%3A2019-11-13&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1188967436118192133-1188968668509589504&q=kincadefire%20since%3A2019-10-28%20until%3A2019-10-29&l=english
INFO: Using proxy 12.218.209.13

INFO: Using proxy 110.5.100.130:60996
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKD9v__zgyEWgMCn7Yva9oMhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-31%20until%3A2019-11-01&l=english
INFO: Using proxy 110.5.100.130:60996
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKb5_KHhjCEWgICnodCn-IwhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-11-06%20until%3A2019-11-08&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKCNneuRjyEWgMC6yaOFu48hEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-11-09%20until%3A2019-11-10&l=english
INFO: 

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaMwL7t1q7i_iAWgoCokbnC4_4gEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-27%20until%3A2019-10-28&l=english
INFO: Using proxy 117.103.5.186:44825
INFO: Using proxy 117.103.5.186:44825
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKiJhpq3jiEWgMC6yaOFu48hEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-11-09%20until%3A2019-11-10&l=english
INFO: Using proxy 117.103.5.186:44825
INFO: Retrying... (Attempts left: 41)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=kincadefire%20since%3A2019-10-23%20until%3A2019-10-24&l=english
INFO: Using proxy 193.110.115.220:3128
INFO: Scraping tweets from https://twitter.com/i/se

INFO: Using proxy 190.5.225.178:53570
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLulicOFiiEWgsCivZ6TroohEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-11-05%20until%3A2019-11-06&l=english
INFO: Using proxy 190.5.225.178:53570
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLS1q_jugyEWgMCn7Yva9oMhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-31%20until%3A2019-11-01&l=english
INFO: Using proxy 190.5.225.178:53570
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLe91avJjCEWgICnodCn-IwhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-11-06

...

INFO: Retrying... (Attempts left: 6)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKeJ4pPT_yAWgMCq-YutiIAhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-28%20until%3A2019-10-29&l=english
INFO: Using proxy 92.86.10.42:42658
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwKrZ8Oe5-iAWgICmyY6O9fogEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-24%20until%3A2019-10-25&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 

INFO: Retrying... (Attempts left: 5)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKeJ4pPT_yAWgMCq-YutiIAhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-28%20until%3A2019-10-29&l=english
INFO: Using proxy 183.87.14.250:44915
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwKrZ8Oe5-iAWgICmyY6O9fogEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-24%20until%3A2019-10-25&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", lin

INFO: Retrying... (Attempts left: 4)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKeJ4pPT_yAWgMCq-YutiIAhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-28%20until%3A2019-10-29&l=english
INFO: Using proxy 83.174.233.94:42323
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwKrZ8Oe5-iAWgICmyY6O9fogEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-24%20until%3A2019-10-25&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", lin

INFO: Retrying... (Attempts left: 3)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKeJ4pPT_yAWgMCq-YutiIAhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-28%20until%3A2019-10-29&l=english
INFO: Using proxy 176.119.134.14:23500
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwKrZ8Oe5-iAWgICmyY6O9fogEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-24%20until%3A2019-10-25&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", li

INFO: Retrying... (Attempts left: 1)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKeJ4pPT_yAWgMCq-YutiIAhEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-28%20until%3A2019-10-29&l=english
INFO: Using proxy 181.52.237.106:58484
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLu9jda5_iAWgoCokbnC4_4gEjUAFQAlAFUAFQAA&q=kincadefire%20since%3A2019-10-27%20until%3A2019-10-28&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", li

In [77]:
df_kincade5=pd.DataFrame(t.__dict__ for t in tweets_kincade)

In [92]:
len(df_kincade5.columns)

21

In [ ]:
#df.loc[(df['column_name'] >= A) & (df['column_name'] <= B)]
#df1 = df[df['A'].map(df['A'].value_counts()) > 1]

In [80]:
df_kincade5['hashtags'] = df_kincade5['hashtags'].astype(str)
df_kincade5['hashtags'] = df_kincade5.hashtags.str.replace('[^a-zA-Z0-9]','')

In [81]:
df_kincade5['img_urls'] = df_kincade5['img_urls'].astype(str)
df_kincade5['img_urls'] = df_kincade5['img_urls'].str.strip('[]').astype(str)

In [82]:
df_kincade5['links'] = df_kincade5['links'].astype(str)
df_kincade5['links'] = df_kincade5['links'].str.strip('[]').astype(str)

In [97]:
cd '/Users/Brian 1/Desktop/GA_12.10_1.04/shelter_status/Data/Fire'

/Users/Brian 1/Desktop/GA_12.10_1.04/shelter_status/Data/Fire


In [102]:
tweets_kincadefire =df_kincade5

In [103]:
tweets_kincadefire.to_csv('../tweets_kincadefire.csv')

In [104]:
df_kincade5['hashtags'].value_counts().head(3)

KincadeFire    4977
kincadefire     686
Kincadefire     177
Name: hashtags, dtype: int64

## CARR FIRE

In [120]:
carr_begin_date = dt.date(2018,7,23)
carr_end_date = dt.date(2018,9,7)  # Jul 23, 2018 – Aug 30, 2018 add one week - September 7, 2018

In [130]:
tweets_carr_fire = query_tweets('carr fire', begindate=carr_begin_date, enddate=carr_end_date,
                     limit=limit, lang=lang)

INFO: queries: ['carr fire since:2018-07-23 until:2018-07-25', 'carr fire since:2018-07-25 until:2018-07-27', 'carr fire since:2018-07-27 until:2018-07-29', 'carr fire since:2018-07-29 until:2018-08-01', 'carr fire since:2018-08-01 until:2018-08-03', 'carr fire since:2018-08-03 until:2018-08-05', 'carr fire since:2018-08-05 until:2018-08-08', 'carr fire since:2018-08-08 until:2018-08-10', 'carr fire since:2018-08-10 until:2018-08-12', 'carr fire since:2018-08-12 until:2018-08-15', 'carr fire since:2018-08-15 until:2018-08-17', 'carr fire since:2018-08-17 until:2018-08-19', 'carr fire since:2018-08-19 until:2018-08-21', 'carr fire since:2018-08-21 until:2018-08-24', 'carr fire since:2018-08-24 until:2018-08-26', 'carr fire since:2018-08-26 until:2018-08-28', 'carr fire since:2018-08-28 until:2018-08-31', 'carr fire since:2018-08-31 until:2018-09-02', 'carr fire since:2018-09-02 until:2018-09-04', 'carr fire since:2018-09-04 until:2018-09-07']
INFO: Querying carr fire since:2018-07-23 un

INFO: Using proxy 12.218.209.130:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1035992818831904768-1036040714662998016&q=carr%20fire%20since%3A2018-08-31%20until%3A2018-09-02&l=english
INFO: Using proxy 12.218.209.130:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1024442931736797190-1024444565263007744&q=carr%20fire%20since%3A2018-07-29%20until%3A2018-08-01&l=english
INFO: Using proxy 12.218.209.130:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1025889725297643521-1025893906410602496&q=carr%20fire%20since%3A2018-08-03%20until%3A2018-08-05&l=

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKaBwcqF5xwWgsCi2e-KmOccEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-09-04%20until%3A2018-09-07&l=english
INFO: Using proxy 110.5.100.130:60996
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwK2VyejFwBwWgMCmgcuAycAcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-05%20until%3A2018-08-08&l=english
INFO: Using proxy 110.5.100.130:60996
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKely9Wd0RwWgICmtc6dptEcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-19%20until%3A2018-08-21&l=english
INFO: 

INFO: Using proxy 117.103.5.186:44825
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgLyRiN6-1xwWgMC70bfa3dccEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-24%20until%3A2018-08-26&l=english
INFO: Using proxy 117.103.5.186:44825
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKON3abYsxwWisC25eyJ2bMcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-07-27%20until%3A2018-07-29&l=english
INFO: Using proxy 190.5.225.178:53570
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwLbhwO793RwWgICo4Yijld4cEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-28

INFO: Using proxy 190.5.225.178:53570
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKe9_4yEsRwWgICm-a68j7EcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-07-25%20until%3A2018-07-27&l=english
INFO: Using proxy 195.69.221.198:54418
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKbJkb2DzBwWgoC8mav0k8wcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-15%20until%3A2018-08-17&l=english
INFO: Using proxy 195.69.221.198:54418
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKeVnMCq4hwWgICojf3ap-McEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-09-

...

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKbRjMjYyhwWgoC8mav0k8wcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-15%20until%3A2018-08-17&l=english
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaMgL2tzLidvBwWgIC8zdHE2rwcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-03%20until%3A2018-08-05&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897, in json
    return complexjson.loads(self.text, **kwargs)
  File "/o

INFO: Using proxy 45.7.238.250:30980
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaIwK3F6NKE0hwWgoCn2e28ktUcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-21%20until%3A2018-08-24&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897, in json
    return complexjson.loads(self.text, **kwargs)
  File "/opt/anaconda3/lib/python3.7/json/__init__.py", line 348, in loads
    return _default_decoder.decode(s)
  File "/opt/anaconda3/lib/python3.7/json/decoder.py", line 337, in decode
    obj, end = self.raw_decode(s, idx=_w(s, 0).end())
  File "/opt/anaconda3/lib/python3.7/

ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKbRjMjYyhwWgoC8mav0k8wcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-15%20until%3A2018-08-17&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897, in json
    return complexjson.loads(self.text, **kwargs)
  File "/opt/anaconda3/lib/python3.7/json/__init__.py", line 348, in loads
    return _default_decoder.decode(s)
  File "/opt/anaconda3/lib/python3.7/json/decoder.py", line 337, in decode
    obj, end = self.raw_decode(s, idx=_w(s, 0).end())
  File "/opt/anaconda3/lib/python3.7/json/decoder.py", line 355, in raw_de

INFO: Retrying... (Attempts left: 3)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKjBgJ7vxxwWgMCnzdjMyckcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-12%20until%3A2018-08-15&l=english
INFO: Using proxy 165.0.75.137:8080
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaMgL2tzLidvBwWgIC8zdHE2rwcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-03%20until%3A2018-08-05&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 

INFO: Retrying... (Attempts left: 1)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKjBgJ7vxxwWgMCnzdjMyckcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-12%20until%3A2018-08-15&l=english
INFO: Using proxy 85.198.133.19:43157
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaIwK3F6NKE0hwWgoCn2e28ktUcEjUAFQAlAFUAFQAA&q=carr%20fire%20since%3A2018-08-21%20until%3A2018-08-24&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", lin

In [131]:
df_carr=pd.DataFrame(t.__dict__ for t in tweets_carr_fire)

In [132]:
df_carr['hashtags'] = df_carr['hashtags'].astype(str)
df_carr['hashtags'] = df_carr.hashtags.str.replace('[^a-zA-Z0-9]','')
df_carr['img_urls'] = df_carr['img_urls'].astype(str)
df_carr['img_urls'] = df_carr['img_urls'].str.strip('[]').astype(str)
df_carr['links'] = df_carr['links'].astype(str)
df_carr['links'] = df_carr['links'].str.strip('[]').astype(str)

In [134]:
df_carr.to_csv('../df_carr.csv')

## THOMAS FIRE

In [3]:
thomas_begin_date = dt.date(2017,12,4)
thomas_end_date = dt.date(2018,1,19)  # 12/04/2017 - 01/12/2018 plus one week 1/19/2018

In [4]:
thomas_fire = query_tweets('thomas fire', begindate= thomas_begin_date, enddate= thomas_end_date,
                           limit=limit, lang=lang)

INFO: queries: ['thomas fire since:2017-12-04 until:2017-12-06', 'thomas fire since:2017-12-06 until:2017-12-08', 'thomas fire since:2017-12-08 until:2017-12-10', 'thomas fire since:2017-12-10 until:2017-12-13', 'thomas fire since:2017-12-13 until:2017-12-15', 'thomas fire since:2017-12-15 until:2017-12-17', 'thomas fire since:2017-12-17 until:2017-12-20', 'thomas fire since:2017-12-20 until:2017-12-22', 'thomas fire since:2017-12-22 until:2017-12-24', 'thomas fire since:2017-12-24 until:2017-12-27', 'thomas fire since:2017-12-27 until:2017-12-29', 'thomas fire since:2017-12-29 until:2017-12-31', 'thomas fire since:2017-12-31 until:2018-01-02', 'thomas fire since:2018-01-02 until:2018-01-05', 'thomas fire since:2018-01-05 until:2018-01-07', 'thomas fire since:2018-01-07 until:2018-01-09', 'thomas fire since:2018-01-09 until:2018-01-12', 'thomas fire since:2018-01-12 until:2018-01-14', 'thomas fire since:2018-01-14 until:2018-01-16', 'thomas fire since:2018-01-16 until:2018-01-19']
INFO

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-947953102640041985-947979978444017665&q=thomas%20fire%20since%3A2017-12-31%20until%3A2018-01-02&l=english
INFO: Using proxy 158.255.249.58:34239
INFO: Using proxy 158.255.249.58:34239
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-945795120028442624-945806255276339200&q=thomas%20fire%20since%3A2017-12-24%20until%3A2017-12-27&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-949754100345815040-949790122010058752&q=thomas%20fire%20since%3A2018-01-05%20until%3A2018-01-07&l=english
INFO: Scraping tweets from http

INFO: Using proxy 84.22.59.202:8080
INFO: Using proxy 84.22.59.202:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLTx2rKUlxoWgICo_fChlZcaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-17%20until%3A2017-12-20&l=english
INFO: Using proxy 84.22.59.202:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgK-VhbiepRoWgICh3YqjqaUaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-29%20until%3A2017-12-31&l=english
INFO: Using proxy 84.22.59.202:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgK-54fSjtxoWgICi5bjcrLcaEjUAFQAlAFUAFQAA&

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLupnumjihoWjICu4Yy5pYoaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-08%20until%3A2017-12-10&l=english
INFO: Using proxy 103.235.199.46:31611
INFO: Using proxy 188.134.16.191:43665
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwLW5squQrhoWgICtma7Fqq4aEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2018-01-05%20until%3A2018-01-07&l=english
INFO: Using proxy 188.134.16.191:43665
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEgL_drKDbhxoWgsC86ent24caEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2

INFO: Using proxy 103.235.199.46:31611
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKKBnLm6uRoWgMCpgY269bkaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2018-01-14%20until%3A2018-01-16&l=english
INFO: Using proxy 103.235.199.46:31611
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLeR4erQohoWhsC1ye373qIaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-27%20until%3A2017-12-29&l=english
INFO: Using proxy 109.110.73.106:32479
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaKwLblvNifnBoWgoC3if-0qJwaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2

...

INFO: Got 729 tweets for thomas%20fire%20since%3A2017-12-04%20until%3A2017-12-06.
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKGd_vyvmRoWgICtpfHP3pkaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-20%20until%3A2017-12-22&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897, in json
    return complexjson.loads(self.text, **kwargs)
  File "/opt/anaconda3/lib/python3.7/json/__init__.py", line 348, in loads
    return _default_decoder.decode(s)
  File "/opt/anaconda3/lib/python3.7/json/decoder.py", line 337, in decode
    obj, end = self.raw_decode(s, idx=_w(s, 

INFO: Retrying... (Attempts left: 1)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKGRyYyAjhoWgoCwsbfmk44aEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-10%20until%3A2017-12-13&l=english
INFO: Using proxy 91.187.116.232:44981
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLuVqPuJoxoWgICh3YqjqaUaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-29%20until%3A2017-12-31&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py"

INFO: Got 768 tweets for thomas%20fire%20since%3A2017-12-15%20until%3A2017-12-17.
INFO: Got 712 tweets for thomas%20fire%20since%3A2017-12-06%20until%3A2017-12-08.
INFO: Got 8624 tweets (768 new).
INFO: Got 9336 tweets (712 new).
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKe1vqGDoRoWhsC1ye373qIaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-27%20until%3A2017-12-29&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897, in json
    return complexjson.loads(self.text, **kwargs)
  File "/opt/anaconda3/lib/python3.7/json/__init__.py", line 348, in loads
    retur

INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKGd_vyvmRoWgICtpfHP3pkaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-20%20until%3A2017-12-22&l=english
INFO: Using proxy 91.187.116.232:44981
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKe1vqGDoRoWhsC1ye373qIaEjUAFQAlAFUAFQAA&q=thomas%20fire%20since%3A2017-12-27%20until%3A2017-12-29&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py"

INFO: Got 785 tweets for thomas%20fire%20since%3A2017-12-20%20until%3A2017-12-22.
INFO: Got 14031 tweets (785 new).


In [5]:
df_thomas=pd.DataFrame(t.__dict__ for t in thomas_fire)

In [8]:
df_thomas['hashtags'] = df_thomas['hashtags'].astype(str)
df_thomas['hashtags'] = df_thomas.hashtags.str.replace('[^a-zA-Z0-9]','')
df_thomas['img_urls'] = df_thomas['img_urls'].astype(str)
df_thomas['img_urls'] = df_thomas['img_urls'].str.strip('[]').astype(str)
df_thomas['links'] = df_thomas['links'].astype(str)
df_thomas['links'] = df_thomas['links'].str.strip('[]').astype(str)

In [10]:
df_thomas.to_csv('../df_thomas.csv')

## COMBINE KINCADE, CARR, THOMAS FIRE DATAFRAMES

In [21]:
pwd

'/Users/Brian 1/Desktop/GA_12.10_1.04/shelter_status/Data'

In [14]:
cd '/Users/Brian 1/Desktop/GA_12.10_1.04/shelter_status/Data'

/Users/Brian 1/Desktop/GA_12.10_1.04/shelter_status/Data


In [18]:
kincade = pd.read_csv('../data/tweets_kincadefire.csv')

In [19]:
carr = pd.read_csv('../data/df_carr.csv')

In [22]:
thomas = pd.read_csv('../data/df_thomas.csv')

In [23]:
kincade.shape

(12676, 22)

In [24]:
carr.shape

(13674, 22)

In [25]:
thomas.shape

(14032, 22)

In [26]:
features = [kincade, carr, thomas]

In [27]:
all_fires =pd.concat(features)

In [29]:
all_fires.shape

(40382, 22)

In [31]:
all_fires.to_csv('../data/all_fires.csv')

## FIRES ALL EXPLORATORY DATA ANALYSIS

In [41]:
floods = pd.read_csv('../data/df_floods.csv')

In [44]:
floods.head(1)

Unnamed: 0      screen_name           username             user_id  \
0           0  ThomasKBullock2  Thomas K. Bullock  813218221603966976   

              tweet_id                                    tweet_url  \
0  1091479641859198976  /ThomasKBullock2/status/1091479641859198976   

             timestamp  timestamp_epochs  \
0  2019-02-01 23:33:19        1549063999   

                                                text  \
0  Lord, I hope not. We don’t need another 500 ye...   

                                           text_html links hashtags  \
0  <p class="TweetTextSize js-tweet-text tweet-te...    []       []   

   has_media img_urls  video_url  likes  retweets  replies  is_replied  \
0      False       []        NaN      1         0        1        True   

   is_reply_to  parent_tweet_id  \
0         True     1.091472e+18   

                                      reply_to_users disaster  
0  [{'screen_name': 'antmasiello', 'user_id': '54...   floods

In [33]:
firefire = pd.read_csv('../data/all_fires.csv')

/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3058: DtypeWarning: Columns (1,5,13,19,20) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [47]:
disaster = 'fire'

In [48]:
firefire['disaster']= disaster

In [37]:
# df.drop(['B', 'C'], axis=1)
firefire= firefire.drop(['Unnamed: 0', 'Unnamed: 0.1'], axis=1)

In [50]:
firefire.to_csv('../data/all_fires.csv')

## DATA CLEANING

In [128]:
df_text = firefire['text']

In [129]:
df_text = pd.DataFrame(df_text)

In [130]:
df_text['text'] = df_text.text.str.replace('[^a-zA-Z0-9]',' ')

In [131]:
df_text

text
0      Sonoma s wineries and restaurants reopen their...
1       Kincadefire if you experienced agricultural l...
2      Last week the Kincade fire swept through Sonom...
3      A special offer from  getharvestcard   for onl...
4      Last week the Kincade fire swept through Sonom...
...                                                  ...
40377  Fantastic news on this Winter Solstice Day  AL...
40378  All Evacuation Orders Lifted  All SB County ma...
40379  SB COUNTY OEM  All Evacuation Orders Lifted  A...
40380  RT  UtahEmergency  Prime example of teamwork a...
40381   ThomasFire Thanks to all the brave firefighte...

[40382 rows x 1 columns]

In [133]:
cv = CountVectorizer(stop_words='english')

In [123]:
cv.fit(df_text)

CountVectorizer(analyzer='word', binary=False, decode_error='strict',
                dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
                lowercase=True, max_df=1.0, max_features=None, min_df=1,
                ngram_range=(1, 1), preprocessor=None, stop_words=None,
                strip_accents=None, token_pattern='(?u)\\b\\w\\w+\\b',
                tokenizer=None, vocabulary=None)

In [124]:
df_text = cv.transform(df_text)

In [125]:
df_text

<1x1 sparse matrix of type '<class 'numpy.int64'>'
	with 1 stored elements in Compressed Sparse Row format>

In [126]:
df_text = pd.DataFrame(df_text.toarray(),
                          columns=cv.get_feature_names())

In [127]:
df_text

text
0     1

In [74]:
dirichlet = LDA(n_components=3, random_state = 42)

In [ ]:
dirichlet()

In [76]:
X, _ = make_multilabel_classification(random_state=0)

In [80]:
dirichlet.fit(firefire)

ValueError: could not convert string to float: 'WineInkByTia'

In [72]:
firefire

screen_name                username       user_id  \
0         WineInkByTia               Tia Butts  1.702786e+07   
1               AOmbud                 AgOmbud  1.118919e+18   
2        BlueStreakSci     Blue Streak Science  1.105013e+09   
3           SherryHuss             Sherry Huss  1.431744e+07   
4        BlueStreakSci     Blue Streak Science  1.105013e+09   
...                ...                     ...           ...   
40377  mariahmarketing              Laura Kath  3.153761e+07   
40378          WxCat62             Cathy Gregg  7.677248e+17   
40379    ericgreenspan  Eric Greenspan 🎸 🏒 🎨 🎣  3.263907e+07   
40380   StateForesters         State Foresters  4.236656e+08   
40381     lilyjuanlily                 lily_li  2.910258e+09   

                  tweet_id                                   tweet_url  \
0      1194032896010358784    /WineInkByTia/status/1194032896010358784   
1      1194027115823484928          /AOmbud/status/1194027115823484928   
2      1194027041835945984   /BlueStreakSci/status/1194027041835945984   
3      1193998143630610432      /SherryHuss/status/1193998143630610432   
4      1193996911981875202   /BlueStreakSci/status/1193996911981875202   
...                    ...                                         ...   
40377   943891188947521536  /mariahmarketing/status/943891188947521536   
40378   943891182106505216          /WxCat62/status/943891182106505216   
40379   943891147163762688    /ericgreenspan/status/943891147163762688   
40380   943891119112425472   /StateForesters/status/943891119112425472   
40381   943891098249732096     /lilyjuanlily/status/943891098249732096   

                 timestamp  timestamp_epochs  \
0      2019-11-11 23:23:21        1573514601   
1      2019-11-11 23:00:23        1573513223   
2      2019-11-11 23:00:05        1573513205   
3      2019-11-11 21:05:15        1573506315   
4      2019-11-11 21:00:21        1573506021   
...                    ...               ...   
40377  2017-12-21 17:09:30        1513876170   
40378  2017-12-21 17:09:29        1513876169   
40379  2017-12-21 17:09:20        1513876160   
40380  2017-12-21 17:09:14        1513876154   
40381  2017-12-21 17:09:09        1513876149   

                                                    text  \
0      Sonoma's wineries and restaurants reopen their...   
1      #Kincadefire if you experienced agricultural l...   
2      Last week the Kincade fire swept through Sonom...   
3      A special offer from @getharvestcard - for onl...   
4      Last week the Kincade fire swept through Sonom...   
...                                                  ...   
40377  Fantastic news on this Winter Solstice Day! AL...   
40378  All Evacuation Orders Lifted  All SB County ma...   
40379  SB COUNTY OEM: All Evacuation Orders Lifted  A...   
40380  RT @UtahEmergency: Prime example of teamwork a...   
40381  #ThomasFire Thanks to all the brave firefighte...   

                                               text_html  \
0      <p class="TweetTextSize js-tweet-text tweet-te...   
1      <p class="TweetTextSize js-tweet-text tweet-te...   
2      <p class="TweetTextSize js-tweet-text tweet-te...   
3      <p class="TweetTextSize js-tweet-text tweet-te...   
4      <p class="TweetTextSize js-tweet-text tweet-te...   
...                                                  ...   
40377  <p class="TweetTextSize js-tweet-text tweet-te...   
40378  <p class="TweetTextSize js-tweet-text tweet-te...   
40379  <p class="TweetTextSize js-tweet-text tweet-te...   
40380  <p class="TweetTextSize js-tweet-text tweet-te...   
40381  <p class="TweetTextSize js-tweet-text tweet-te...   

                                                   links     hashtags  \
0      'https://www.winespectator.com/articles/sonoma...  KincadeFire   
1                             'http://ow.ly/Z2tJ50x7VMK'  Kincadefire   
2          'https://bluestreakscience.com/applepodcasts'  kincadefire   
3      'https://getharvestcard.com/', 'htt

In [ ]:
"""
df_kfire3 = df_kincade3[df_kincade3['hashtags'].map(df_kincade3['hashtags'].value_counts()) == 4784]
print(df.loc[df['B'].isin(['one','three'])])
result = sr.str.contains(pat = 'is') 
df[df['model'].str.match('Mac')]
df[df.City.str.contains('ville',case=False)]
# Use regular expressions to do a find-and-replace
letters_only = re.sub("[^a-zA-Z]",           # The pattern to search for
                      " ",                   # The pattern to replace it with
                      example1.get_text())   # The text to search
data['result'] = data['result'].map(lambda x: x.lstrip('+-').rstrip('aAbBcC'))

i'd use the pandas replace function, very simple and powerful as you can use regex. Below i'm using the regex \D to remove any non-digit characters but obviously you could get quite creative with regex.

data['result'].replace(regex=True,inplace=True,to_replace=r'\D',value=r'')
df['A1'].str.replace('*','').astype(float)

df['A1'].replace(regex=True, inplace=True, to_replace=r'[^0-9.\-]', value=r'']
                 df.strings.str.replace('[^a-zA-Z]', '')
df.Geo.str.replace("[({':]", "")
"""

## CAMP FIRE 

In [105]:
camp_begin_date = dt.date(2018,11,8)
camp_end_date = dt.date(2019,12,2)

In [106]:
tweets_campfire = query_tweets('campfire', begindate=camp_begin_date, enddate=camp_end_date,
                     limit=limit, lang=lang) ## November 8-25, 2018 add one week for end date so dec. 2

INFO: queries: ['campfire since:2018-11-08 until:2018-11-27', 'campfire since:2018-11-27 until:2018-12-16', 'campfire since:2018-12-16 until:2019-01-05', 'campfire since:2019-01-05 until:2019-01-24', 'campfire since:2019-01-24 until:2019-02-13', 'campfire since:2019-02-13 until:2019-03-04', 'campfire since:2019-03-04 until:2019-03-24', 'campfire since:2019-03-24 until:2019-04-12', 'campfire since:2019-04-12 until:2019-05-02', 'campfire since:2019-05-02 until:2019-05-21', 'campfire since:2019-05-21 until:2019-06-09', 'campfire since:2019-06-09 until:2019-06-29', 'campfire since:2019-06-29 until:2019-07-18', 'campfire since:2019-07-18 until:2019-08-07', 'campfire since:2019-08-07 until:2019-08-26', 'campfire since:2019-08-26 until:2019-09-15', 'campfire since:2019-09-15 until:2019-10-04', 'campfire since:2019-10-04 until:2019-10-24', 'campfire since:2019-10-24 until:2019-11-12', 'campfire since:2019-11-12 until:2019-12-02']
INFO: Querying campfire since:2019-01-24 until:2019-02-13
INFO: 

INFO: Using proxy 12.218.209.130:53281
INFO: Using proxy 12.218.209.130:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1095462764854689792-1095472292744720386&q=campfire%20since%3A2019-01-24%20until%3A2019-02-13&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1067203898031493120-1067206243775705088&q=campfire%20since%3A2018-11-08%20until%3A2018-11-27&l=english
INFO: Using proxy 12.218.209.130:53281
INFO: Using proxy 12.218.209.130:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1151633948914716673-1151642495207563264&q=campfire%20since%3A2019

INFO: Using proxy 110.5.100.130:60996
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwLzFsr62-x8WgIC7se2vuvsfEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-06-29%20until%3A2019-07-18&l=english
INFO: Using proxy 110.5.100.130:60996
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwLbRy7GmmB8WhIC_pdWhqZgfEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-04-12%20until%3A2019-05-02&l=english
INFO: Using proxy 110.5.100.130:60996
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKOlob2L5h4WkIC8jaOcjuYeEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-03-04%20until%

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKbtot-6zx0WgMCj5ZSbvc8dEjUAFQAlAFUAFQAA&q=campfire%20since%3A2018-11-08%20until%3A2018-11-27&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEgLz1xrfSgR4WjMC71Y2T2IEeEjUAFQAlAFUAFQAA&q=campfire%20since%3A2018-12-16%20until%3A2019-01-05&l=english
INFO: Using proxy 117.103.5.186:44825
INFO: Using proxy 117.103.5.186:44825
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKKFmofz5x0WgIC28euu-OcdEjUAFQAlAFUAFQAA&q=campfire%20since%3A2018-11-27%20until%3A2018-12-16&l=english
INFO: Using pro

INFO: Using proxy 195.69.221.198:54418
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwLbxkaHXsB8WgMCn1fuc5LAfEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-05-02%20until%3A2019-05-21&l=english
INFO: Using proxy 195.69.221.198:54418
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKf9ivKq-x8WgIC7se2vuvsfEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-06-29%20until%3A2019-07-18&l=english
INFO: Using proxy 195.69.221.198:54418
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKKxx9yLmh4WhIC_3bqjk5oeEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-01-05%20unt

...

INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLu5wsv95B4WkIC8jaOcjuYeEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-03-04%20until%3A2019-03-24&l=english
INFO: Using proxy 175.100.72.95:58667
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLyxmra1lx8WhIC_pdWhqZgfEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-04-12%20until%3A2019-05-02&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897,

INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaMwLTlwPSXyx4WgoC88bCirsweEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-02-13%20until%3A2019-03-04&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKLRp5izxiAWgMC67dz5tMcgEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-08-26%20until%3A2019-09-15&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKLVroT1-CAWgoC79eWs0PkgEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-10-04%20until%3A2019-10-24&l=english
INFO: Scraping tweets from https://twitter.com/i/searc

INFO: Got 710 tweets for campfire%20since%3A2019-10-24%20until%3A2019-11-12.
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLu5wsv95B4WkIC8jaOcjuYeEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-03-04%20until%3A2019-03-24&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897, in json
    return complexjson.loads(self.text, **kwargs)
  File "/opt/anaconda3/lib/python3.7/json/__init__.py", line 348, in loads
    return _default_decoder.decode(s)
  File "/opt/anaconda3/lib/python3.7/json/decoder.py", line 337, in decode
    obj, end = self.raw_decode(s, idx=_w(s, 0).end())


ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLTd5_nvsh4WhMCn5eCP87MeEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-01-24%20until%3A2019-02-13&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897, in json
    return complexjson.loads(self.text, **kwargs)
  File "/opt/anaconda3/lib/python3.7/json/__init__.py", line 348, in loads
    return _default_decoder.decode(s)
  File "/opt/anaconda3/lib/python3.7/json/decoder.py", line 337, in decode
    obj, end = self.raw_decode(s, idx=_w(s, 0).end())
  File "/opt/anaconda3/lib/python3.7/json/decoder.py", line 355, in raw_decod

INFO: Got 651 tweets for campfire%20since%3A2018-11-08%20until%3A2018-11-27.
ERROR: Failed to parse JSON "Expecting value: line 1 column 1 (char 0)" while requesting "https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLuV_J6uyB8WgsC1pbGyn8kfEjUAFQAlAFUAFQAA&q=campfire%20since%3A2019-05-21%20until%3A2019-06-09&l=english"
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/twitterscraper/query.py", line 99, in query_single_page
    json_resp = response.json()
  File "/opt/anaconda3/lib/python3.7/site-packages/requests/models.py", line 897, in json
    return complexjson.loads(self.text, **kwargs)
  File "/opt/anaconda3/lib/python3.7/json/__init__.py", line 348, in loads
    return _default_decoder.decode(s)
  File "/opt/anaconda3/lib/python3.7/json/decoder.py", line 337, in decode
    obj, end = self.raw_decode(s, idx=_w(s, 0).end())


In [107]:
df_campfire=pd.DataFrame(t.__dict__ for t in tweets_campfire)

In [109]:
df_campfire['hashtags'] = df_campfire['hashtags'].astype(str)
df_campfire['hashtags'] = df_campfire.hashtags.str.replace('[^a-zA-Z0-9]','')
df_campfire['img_urls'] = df_campfire['img_urls'].astype(str)
df_campfire['img_urls'] = df_campfire['img_urls'].str.strip('[]').astype(str)
df_campfire['links'] = df_campfire['links'].astype(str)
df_campfire['links'] = df_campfire['links'].str.strip('[]').astype(str)

In [94]:
#needs_kincade = df_kincade5[df_kincade5['text'].str.contains('need')]

In [91]:
import re

regex = re.compile('[^a-zA-Z0-9]')

l = ["a#bc1!","a(b$c"]

print [regex.sub('', i) for i in l]

['abc', 'abc']

SyntaxError: invalid syntax (<ipython-input-91-df18b00dbef3>, line 7)

In [128]:
pwd

'/Users/Brian 1/Desktop/GA_12.10_1.04/shelter_status/Data/Fire'

In [41]:
# df.to_csv(r'Path where you want to store the exported CSV file\File Name.csv')
df_kincade2.to_csv('../Data/kincade.csv')

In [27]:
#df[df['model'].str.contains('ac')]
#df.loc[df['username'] == some_value]
df_kincade2[df_kincade['username'].str.contains('shelter')]

Empty DataFrame
Columns: [screen_name, username, user_id, tweet_id, tweet_url, timestamp, timestamp_epochs, text, text_html, links, hashtags, has_media, img_urls, video_url, likes, retweets, replies, is_replied, is_reply_to, parent_tweet_id, reply_to_users]
Index: []

In [10]:
tweets_RedCrossNorCal = query_tweets('RedCrossNorCal', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['RedCrossNorCal since:2019-10-23 until:2019-10-26', 'RedCrossNorCal since:2019-10-26 until:2019-10-29', 'RedCrossNorCal since:2019-10-29 until:2019-11-02', 'RedCrossNorCal since:2019-11-02 until:2019-11-05', 'RedCrossNorCal since:2019-11-05 until:2019-11-09', 'RedCrossNorCal since:2019-11-09 until:2019-11-12', 'RedCrossNorCal since:2019-11-12 until:2019-11-16', 'RedCrossNorCal since:2019-11-16 until:2019-11-19', 'RedCrossNorCal since:2019-11-19 until:2019-11-23', 'RedCrossNorCal since:2019-11-23 until:2019-11-26', 'RedCrossNorCal since:2019-11-26 until:2019-11-29', 'RedCrossNorCal since:2019-11-29 until:2019-12-03', 'RedCrossNorCal since:2019-12-03 until:2019-12-06', 'RedCrossNorCal since:2019-12-06 until:2019-12-10', 'RedCrossNorCal since:2019-12-10 until:2019-12-13', 'RedCrossNorCal since:2019-12-13 until:2019-12-17', 'RedCrossNorCal since:2019-12-17 until:2019-12-20', 'RedCrossNorCal since:2019-12-20 until:2019-12-24', 'RedCrossNorCal since:2019-12-24 until:2019-12-2

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1205358565722148864-1205647214137110528&q=RedCrossNorCal%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1205027758746882048-1205114925846351874&q=RedCrossNorCal%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1198043842072760320-1199082866409426944&q=RedCrossNorCal%20since%3A2019-11-23%20until%3A2019-11-26&l=english
INFO: Using proxy 91.226.3

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1196965410823974913-1198008065125048320&q=RedCrossNorCal%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLSV-PnvkiEWgoC3ncva8JYhEjUAFQAlAFUAFQAA&q=RedCrossNorCal%20since%3A2019-11-12%20until%3A2019-11-16&l=english
INFO: Using proxy 195.228.65.108:52378
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1189767218084474885-1190417271757385729&q=RedCrossNorCal%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using pro

INFO: Got 53 tweets for RedCrossNorCal%20since%3A2019-11-19%20until%3A2019-11-23.
INFO: Got 284 tweets (53 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLfFzO7X-CAWgICo6YqnmfwgEjUAFQAlAFUAFQAA&q=RedCrossNorCal%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 204.15.243.234:40860
INFO: Twitter returned : 'has_more_items' 
INFO: Got 60 tweets for RedCrossNorCal%20since%3A2019-10-23%20until%3A2019-10-26.
INFO: Got 344 tweets (60 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLvx77n__iAWgMCq9YqXh4AhEjUAFQAlAFUAFQAA&q=RedCrossNorCal%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&

In [11]:
tweets_RedCrossNorCal= pd.DataFrame(t.__dict__ for t in tweets_RedCrossNorCal)

In [12]:
tweets_RedCrossNorCal.shape

(756, 21)

In [13]:
tweets_RedCrossNorCal.to_csv('../Data/tweets_RedCrossNorCal.csv')

In [ ]:
# RedCrossNorCal, CalFireNews, BCWildfireWkly, CountofSonoma
# NorthBayNews, KQEDnews, NorCalFireList, UpfrontKPRA, CAPublicHealth, KQED

In [14]:
tweets_CalFireNews = query_tweets('CalFireNews', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['CalFireNews since:2019-10-23 until:2019-10-26', 'CalFireNews since:2019-10-26 until:2019-10-29', 'CalFireNews since:2019-10-29 until:2019-11-02', 'CalFireNews since:2019-11-02 until:2019-11-05', 'CalFireNews since:2019-11-05 until:2019-11-09', 'CalFireNews since:2019-11-09 until:2019-11-12', 'CalFireNews since:2019-11-12 until:2019-11-16', 'CalFireNews since:2019-11-16 until:2019-11-19', 'CalFireNews since:2019-11-19 until:2019-11-23', 'CalFireNews since:2019-11-23 until:2019-11-26', 'CalFireNews since:2019-11-26 until:2019-11-29', 'CalFireNews since:2019-11-29 until:2019-12-03', 'CalFireNews since:2019-12-03 until:2019-12-06', 'CalFireNews since:2019-12-06 until:2019-12-10', 'CalFireNews since:2019-12-10 until:2019-12-13', 'CalFireNews since:2019-12-13 until:2019-12-17', 'CalFireNews since:2019-12-17 until:2019-12-20', 'CalFireNews since:2019-12-20 until:2019-12-24', 'CalFireNews since:2019-12-24 until:2019-12-27', 'CalFireNews since:2019-12-27 until:2019-12-31']
INFO

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1195135403218608129-1195490875108773888&q=CalFireNews%20since%3A2019-11-12%20until%3A2019-11-16&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1195757362335772672-1196576028946075648&q=CalFireNews%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1199898999811006464-1200139365067788288&q=CalFireNews%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Scraping tweets from https://

INFO: Using proxy 195.228.65.108:52378
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKqRw_XetyEWnMC19amR7bkhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 195.228.65.108:52378
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKbdj-GxmyEWgMCj6cSfkaAhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 195.228.65.108:52378
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKj5t9q7oiEWgsC0sdKuiKQhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-11

INFO: Using proxy 138.121.32.26:23500
INFO: Using proxy 138.121.32.26:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKfJgaSflyEWgMCggeDji5shEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Using proxy 138.121.32.26:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKedparXpSEWgMCm-YHL-qchEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 138.121.32.26:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKbl8c-6qyEWgsC93cz5hq0hEjUAFQAlAFUAF

INFO: Using proxy 177.53.8.125:47970
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKOJg4rMgyEWhIC7qYf9moUhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKal4MeE_yAWgICn-dCYiIAhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 177.53.8.125:47970
INFO: Using proxy 177.53.8.125:47970
INFO: Twitter returned : 'has_more_items' 
INFO: Got 79 tweets for CalFireNews%20since%3A2019-12-27%20until%3A2019-12-31.
INFO: Got 537 tweets (79 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&incl

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKep-_iu-iAWgMCi4YPFlfwgEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Twitter returned : 'has_more_items' 
INFO: Got 135 tweets for CalFireNews%20since%3A2019-11-02%20until%3A2019-11-05.
INFO: Got 973 tweets (135 new).
INFO: Using proxy 148.77.34.194:39175
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLTBrs2vgyEWhIC7qYf9moUhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 148.77.34.194:39175
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=

INFO: Using proxy 1.20.102.228:59054
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLXN8OShgSEWhIC7qYf9moUhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 31.28.99.25:43760
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwKaVss3N_SAWgICn-dCYiIAhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 31.28.99.25:43760
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLu1osT7gCEWhIC7qYf9moUhEjUAFQAlAFUAFQAA&q=CalFireNews%20since%3A2019-10-29%20un

In [20]:
type(tweets_CalFireNews)

pandas.core.frame.DataFrame

In [17]:
tweets_CalFireNews.to_csv('../Data/tweets_CalFireNews.csv')

In [21]:
tweets_BCWildfireWkly = query_tweets('BCWildfireWkly', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['BCWildfireWkly since:2019-10-23 until:2019-10-26', 'BCWildfireWkly since:2019-10-26 until:2019-10-29', 'BCWildfireWkly since:2019-10-29 until:2019-11-02', 'BCWildfireWkly since:2019-11-02 until:2019-11-05', 'BCWildfireWkly since:2019-11-05 until:2019-11-09', 'BCWildfireWkly since:2019-11-09 until:2019-11-12', 'BCWildfireWkly since:2019-11-12 until:2019-11-16', 'BCWildfireWkly since:2019-11-16 until:2019-11-19', 'BCWildfireWkly since:2019-11-19 until:2019-11-23', 'BCWildfireWkly since:2019-11-23 until:2019-11-26', 'BCWildfireWkly since:2019-11-26 until:2019-11-29', 'BCWildfireWkly since:2019-11-29 until:2019-12-03', 'BCWildfireWkly since:2019-12-03 until:2019-12-06', 'BCWildfireWkly since:2019-12-06 until:2019-12-10', 'BCWildfireWkly since:2019-12-10 until:2019-12-13', 'BCWildfireWkly since:2019-12-13 until:2019-12-17', 'BCWildfireWkly since:2019-12-17 until:2019-12-20', 'BCWildfireWkly since:2019-12-20 until:2019-12-24', 'BCWildfireWkly since:2019-12-24 until:2019-12-2

INFO: Using proxy 91.226.35.93:53281
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1192518646242803713-1192950368340037633&q=BCWildfireWkly%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1190360947287707653-1190417390049169409&q=BCWildfireWkly%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1203775662126796801-1204172824698478592&q=BCWildfireWkly%20si

INFO: Using proxy 195.228.65.108:52378
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKDB6Ly3zSEWgoC2saaAjdEhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-12-27%20until%3A2019-12-31&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKPR27apoSEWhMCg0fSVjqQhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-11-23%20until%3A2019-11-26&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKPt2OW6riEWgICo1erW67AhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-12-03%20until%3A2019-12-06&l=english
INFO: Using proxy 195.228.65.108:5

INFO: Using proxy 138.121.32.26:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKLl55_lsyEWgICnhbuzirYhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Using proxy 138.121.32.26:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEgKbd_sXqpiEWgsCq8dXJ-qchEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Twitter returned : 'has_more_items' 
INFO: Using proxy 138.121.32.26:23500
INFO: Got 56 tweets for BCWildfireWkly%20since%3A2019-12-03%20until%3A2019-12-06.
INFO: Got 248 tweets (56 new).
INFO: Twitter returned : 'has_more_items' 
INFO: Got 57 tweets for BCWildfireWkly%20since%3A2019-11-16%20until%3

INFO: Using proxy 177.53.8.125:47970
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKeN5pyj-yAWgMCq4eeml_wgEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 177.53.8.125:47970
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKqBs4e1hyEWiIC3scSEhIkhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-11-02%20until%3A2019-11-05&l=english
INFO: Using proxy 177.53.8.125:47970
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKbFydDDhCEWgsCgxeSTm4UhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019

INFO: Using proxy 91.135.148.198:59384
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKqVhMXz-iAWgMCq4eeml_wgEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 148.77.34.194:39175
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKPh3tn7_iAWgMCj-ZiRhIAhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 148.77.34.194:39175
INFO: Twitter returned : 'has_more_items' 
INFO: Got 123 tweets for BCWildfireWkly%20since%3A2019-11-05%20until%3A2019-11-09.
INFO: Got 981 tweets (123 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_

INFO: Using proxy 1.20.102.228:59054
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKb9u7zSgiEWgsCgxeSTm4UhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 1.20.102.228:59054
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKf9-KCM_iAWgMCj-ZiRhIAhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 31.28.99.25:43760
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLad39vGgiEWgsCgxeSTm4UhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-

INFO: Got 421 tweets for BCWildfireWkly%20since%3A2019-10-26%20until%3A2019-10-29.
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwLTNze_PgCEWgsCgxeSTm4UhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 202.166.220.150:32324
INFO: Got 2141 tweets (421 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLXBi7mMgCEWgsCgxeSTm4UhEjUAFQAlAFUAFQAA&q=BCWildfireWkly%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 103.35.132.145:36555
INFO: Twitter returned : 'has_more_items' 
INFO: Got 442 tweets for BCWildfireWkly%20since%3A2019-10-29%20until%3A2019-11-02.
INFO: Got 2583 tweets (442 new).


In [22]:
tweets_BCWildfireWkly= pd.DataFrame(t.__dict__ for t in tweets_BCWildfireWkly)

In [23]:
tweets_BCWildfireWkly.shape   # there are tweets that are not from BCWildfireWkly and I'm not sure why

(2583, 21)

In [24]:
tweets_BCWildfireWkly.to_csv('../Data/BCWildfireWkly.csv')

In [25]:
tweets_CountyofSonoma = query_tweets('CountyofSonoma', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['CountyofSonoma since:2019-10-23 until:2019-10-26', 'CountyofSonoma since:2019-10-26 until:2019-10-29', 'CountyofSonoma since:2019-10-29 until:2019-11-02', 'CountyofSonoma since:2019-11-02 until:2019-11-05', 'CountyofSonoma since:2019-11-05 until:2019-11-09', 'CountyofSonoma since:2019-11-09 until:2019-11-12', 'CountyofSonoma since:2019-11-12 until:2019-11-16', 'CountyofSonoma since:2019-11-16 until:2019-11-19', 'CountyofSonoma since:2019-11-19 until:2019-11-23', 'CountyofSonoma since:2019-11-23 until:2019-11-26', 'CountyofSonoma since:2019-11-26 until:2019-11-29', 'CountyofSonoma since:2019-11-29 until:2019-12-03', 'CountyofSonoma since:2019-12-03 until:2019-12-06', 'CountyofSonoma since:2019-12-06 until:2019-12-10', 'CountyofSonoma since:2019-12-10 until:2019-12-13', 'CountyofSonoma since:2019-12-13 until:2019-12-17', 'CountyofSonoma since:2019-12-17 until:2019-12-20', 'CountyofSonoma since:2019-12-20 until:2019-12-24', 'CountyofSonoma since:2019-12-24 until:2019-12-2

INFO: Using proxy 91.226.35.93:53281
INFO: Twitter returned : 'has_more_items' 
INFO: Got 8 tweets for CountyofSonoma%20since%3A2019-11-29%20until%3A2019-12-03.
INFO: Got 8 tweets (8 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1208060501541810176-1209247532309565441&q=CountyofSonoma%20since%3A2019-12-20%20until%3A2019-12-24&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1204452033316577280-1204819942723354625&q=CountyofSonoma%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=

INFO: Using proxy 195.228.65.108:52378
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKOV2uWEuiEWgMCi4Y_g774hEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 195.228.65.108:52378
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKe1i66E_CAWgMCqwbvYlfwgEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 195.228.65.108:52378
INFO: Twitter returned : 'has_more_items' 
INFO: Got 32 tweets for CountyofSonoma%20since%3A2019-12-10%20until%3A2019-12-13.
INFO: Got 158 tweets (32 new).
INFO: Twitter returned : 'has_more_items' 
INFO: Got 34 tweets for CountyofSonoma%20since%3A2019-12-13%20unti

INFO: Using proxy 138.121.32.26:23500
INFO: Twitter returned : 'has_more_items' 
INFO: Got 54 tweets for CountyofSonoma%20since%3A2019-12-17%20until%3A2019-12-20.
INFO: Got 407 tweets (54 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKj1jrnj-yAWgMCqwbvYlfwgEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 204.15.243.234:40860
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKqh3_LXhyEWgsCjwev3hYkhEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-11-02%20until%3A2019-11-05&l=english
INFO: Using proxy 204.15.243.234:40860
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_f

INFO: Using proxy 148.77.34.194:39175
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgLu5ydvjgiEWgsCq_czwmYUhEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 148.77.34.194:39175
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKf19eiK_yAWgMC84cPKhoAhEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 148.77.34.194:39175
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKD5neTa-iAWgMCqwbvYlfwgEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2

INFO: Using proxy 36.67.226.17:37860
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKeBq7j6-SAWgMCqwbvYlfwgEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 46.180.156.230:35808
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaGwKK9t6G1_iAWgMC84cPKhoAhEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 46.180.156.230:35808
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLXR7NqxgSEWgsCq_czwmYUhEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A

INFO: Using proxy 175.41.44.51:52581
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLuZwufH_SAWgMC84cPKhoAhEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 128.0.179.234:41258
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaKwKrhyI6MgCEWgsCq_czwmYUhEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 128.0.179.234:41258
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKbZq52LgCEWgsCq_czwmYUhEjUAFQAlAFUAFQAA&q=CountyofSonoma%20since%3A20

In [26]:
tweets_CountyofSonoma= pd.DataFrame(t.__dict__ for t in tweets_CountyofSonoma)

In [27]:
tweets_CountyofSonoma.shape

(2184, 21)

In [28]:
tweets_CountyofSonoma.to_csv('../Data/tweets_CountyofSonoma.csv')

In [29]:
tweets_NorthBayNews = query_tweets('NorthBayNews', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['NorthBayNews since:2019-10-23 until:2019-10-26', 'NorthBayNews since:2019-10-26 until:2019-10-29', 'NorthBayNews since:2019-10-29 until:2019-11-02', 'NorthBayNews since:2019-11-02 until:2019-11-05', 'NorthBayNews since:2019-11-05 until:2019-11-09', 'NorthBayNews since:2019-11-09 until:2019-11-12', 'NorthBayNews since:2019-11-12 until:2019-11-16', 'NorthBayNews since:2019-11-16 until:2019-11-19', 'NorthBayNews since:2019-11-19 until:2019-11-23', 'NorthBayNews since:2019-11-23 until:2019-11-26', 'NorthBayNews since:2019-11-26 until:2019-11-29', 'NorthBayNews since:2019-11-29 until:2019-12-03', 'NorthBayNews since:2019-12-03 until:2019-12-06', 'NorthBayNews since:2019-12-06 until:2019-12-10', 'NorthBayNews since:2019-12-10 until:2019-12-13', 'NorthBayNews since:2019-12-13 until:2019-12-17', 'NorthBayNews since:2019-12-17 until:2019-12-20', 'NorthBayNews since:2019-12-20 until:2019-12-24', 'NorthBayNews since:2019-12-24 until:2019-12-27', 'NorthBayNews since:2019-12-27 unt

INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1202666336419078144-1202737861964918786&q=NorthBayNews%20since%3A2019-12-03%20until%3A2019-12-06&l=english
INFO: Using proxy 91.226.35.93:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1195442531472834560-1195489799395627008&q=NorthBayNews%20since%3A2019-11-12%20until%3A2019-11-16&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1204103807493271552-1204182790528389120&q=NorthBayNews%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Using proxy 91.226.35.93:5

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKbp6pHxviEWgMCmlYy6kL8hEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEgKaxiJTl0CEWjIC76dj8jdEhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-12-27%20until%3A2019-12-31&l=english
INFO: Using proxy 195.228.65.108:52378
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgLepj931jSEWgICmzeTJmY4hEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Using proxy 195.228.65.108:52378
I

INFO: Using proxy 138.121.32.26:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKPJp4LQmiEWgsCj-ayBjJshEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Using proxy 138.121.32.26:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwLTV2vzPjSEWgICmzeTJmY4hEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Using proxy 138.121.32.26:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKiRnJOCrCEWgMC6yY7biK0hEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11

INFO: Using proxy 204.15.243.234:40860
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKfZqc3huCEWgMCg9b7E_7khEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 177.53.8.125:47970
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKP166Ph_yAWgMCq1aOjh4AhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaIwL69nYGiqyEWgMC6yY7biK0hEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11-29%20until%3A2019-12-03&l=english
INF

...

INFO: Using proxy 36.67.226.17:37860
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgLbdh6v5myEWhMCj4ff8n6AhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 46.180.156.230:35808
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKq1pMmplyEWgsCj-ayBjJshEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Using proxy 36.67.226.17:37860
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLWZrbqdkyEWgMCime_onZchEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11-

INFO: Using proxy 78.130.145.167:40406
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKP1y4vl_iAWgMCq1aOjh4AhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 78.130.145.167:40406
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEgLfhz5qOiiEWgICmzeTJmY4hEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Using proxy 78.130.145.167:40406
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKbh9LeV-iAWgIColezcl_wgEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019

INFO: Using proxy 103.35.132.145:36555
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwKq9q938-SAWgIColezcl_wgEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 175.41.44.51:52581
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKeR58jqgSEWgMCjgcGzmoUhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 175.41.44.51:52581
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKOh18rI_iAWgMCq1aOjh4AhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-

INFO: Using proxy 186.233.98.173:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgL_RxNv1gCEWgMCjgcGzmoUhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 186.233.98.173:23500
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKDVzYCo_iAWgMCq1aOjh4AhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 212.95.180.50:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKfRyLDlgCEWgMCjgcGzmoUhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-

INFO: Using proxy 37.220.195.14:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLbBkpqj_CAWgMCq1aOjh4AhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 194.183.168.129:31385
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwKPlmJua_CAWgMCq1aOjh4AhEjUAFQAlAFUAFQAA&q=NorthBayNews%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 5.202.181.169:8080
INFO: Twitter returned : 'has_more_items' 
INFO: Got 993 tweets for NorthBayNews%20since%3A2019-10-26%20until%3A2019-10-29.
INFO: Got 6401 tweets (993 new).


In [30]:
tweets_NorthBayNews= pd.DataFrame(t.__dict__ for t in tweets_NorthBayNews)

In [31]:
tweets_NorthBayNews.shape

(6401, 21)

In [32]:
tweets_NorthBayNews.to_csv('../Data/tweets_NorthBayNews.csv')

In [10]:
tweets_KQEDnews = query_tweets('KQEDnews', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['KQEDnews since:2019-10-23 until:2019-10-26', 'KQEDnews since:2019-10-26 until:2019-10-29', 'KQEDnews since:2019-10-29 until:2019-11-02', 'KQEDnews since:2019-11-02 until:2019-11-05', 'KQEDnews since:2019-11-05 until:2019-11-09', 'KQEDnews since:2019-11-09 until:2019-11-12', 'KQEDnews since:2019-11-12 until:2019-11-16', 'KQEDnews since:2019-11-16 until:2019-11-19', 'KQEDnews since:2019-11-19 until:2019-11-23', 'KQEDnews since:2019-11-23 until:2019-11-26', 'KQEDnews since:2019-11-26 until:2019-11-29', 'KQEDnews since:2019-11-29 until:2019-12-03', 'KQEDnews since:2019-12-03 until:2019-12-06', 'KQEDnews since:2019-12-06 until:2019-12-10', 'KQEDnews since:2019-12-10 until:2019-12-13', 'KQEDnews since:2019-12-13 until:2019-12-17', 'KQEDnews since:2019-12-17 until:2019-12-20', 'KQEDnews since:2019-12-20 until:2019-12-24', 'KQEDnews since:2019-12-24 until:2019-12-27', 'KQEDnews since:2019-12-27 until:2019-12-31']
INFO: Querying KQEDnews since:2019-10-29 until:2019-11-02
INFO: 

INFO: Using proxy 47.56.108.182:8118
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1197938796341293057-1198017699101716486&q=KQEDnews%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 47.56.108.182:8118
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1196542592285958144-1196577324885397504&q=KQEDnews%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Using proxy 47.56.108.182:8118
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1207703498222997505-1207811973322137600&q=KQEDnews%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: U

INFO: Using proxy 103.209.64.19:6666
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwKepoL_3nyEWjMC12f-vm6AhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 103.209.64.19:6666
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKOB45rnviEWgMCirf-8jb8hEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 103.209.64.19:6666
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwKO1rY3poyEWgMCjnYaNjKQhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-23%20until%3A2

INFO: Using proxy 196.216.220.201:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKbpkonZoyEWgMCjnYaNjKQhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-23%20until%3A2019-11-26&l=english
INFO: Using proxy 196.216.220.201:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKOJmN3ouCEWgoCjxbWCgLohEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 196.216.220.201:53281
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLadqfLoliEWgsC-pezKm5chEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-12%20

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKbRyPe7hyEWgMCi0f-NiYkhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-02%20until%3A2019-11-05&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKbx0s_KtCEWgICm7YGakbYhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaKwLWFvt3tjCEWgoCoody8nI4hEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Scrapin

...

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKPp75GflCEWgsC-pezKm5chEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-12%20until%3A2019-11-16&l=english
INFO: Using proxy 203.202.254.206:61456
INFO: Using proxy 203.202.254.206:61456
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgKjN45TzwyEWhMCi9abnkcghEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-12-20%20until%3A2019-12-24&l=english
INFO: Using proxy 203.202.254.206:61456
INFO: Twitter returned : 'has_more_items' 
INFO: Got 135 tweets for KQEDnews%20since%3A2019-12-10%20until%3A2019-12-13.
INFO: Got 943 tweets (135 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&in

INFO: Using proxy 84.75.180.219:80
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKbFi_-8gSEWgMCgqdSflYUhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 84.75.180.219:80
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLSVtZKdhSEWgMCi0f-NiYkhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-02%20until%3A2019-11-05&l=english
INFO: Using proxy 124.41.211.196:36084
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgLe11ZGo_iAWgMC88cT-hoAhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-10-26%20until%3A201

INFO: Using proxy 175.184.232.62:8888
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaMwLrRhbWXnCEWjMC12f-vm6AhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 175.184.232.62:8888
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKa1tJGejiEWgMCqjbPKipIhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-09%20until%3A2019-11-12&l=english
INFO: Using proxy 93.64.183.162:56508
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKedtdzViyEWgoCoody8nI4hEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-11-05%20until%

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKqRh4Pk-SAWhICmjajhmfwgEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 159.203.25.42:8118
INFO: Twitter returned : 'has_more_items' 
INFO: Got 248 tweets for KQEDnews%20since%3A2019-11-19%20until%3A2019-11-23.
INFO: Got 2768 tweets (248 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKj9pImh_CAWgMC88cT-hoAhEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 159.203.25.42:8118
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=

INFO: Using proxy 77.38.21.239:8080
INFO: Twitter returned : 'has_more_items' 
INFO: Got 515 tweets for KQEDnews%20since%3A2019-11-05%20until%3A2019-11-09.
INFO: Got 3626 tweets (515 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKOxqeWs-SAWhICmjajhmfwgEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 95.156.125.190:41870
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaKwKPtzbeb-SAWhICmjajhmfwgEjUAFQAlAFUAFQAA&q=KQEDnews%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 118.173.233.39:48988
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include

In [11]:
tweets_KQEDnews= pd.DataFrame(t.__dict__ for t in tweets_KQEDnews)

In [12]:
tweets_KQEDnews.shape

(4234, 21)

In [13]:
tweets_KQEDnews.to_csv('../Data/tweets_KQEDnews.csv')

In [14]:
tweets_NorCalFireList = query_tweets('NorCalFireList', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['NorCalFireList since:2019-10-23 until:2019-10-26', 'NorCalFireList since:2019-10-26 until:2019-10-29', 'NorCalFireList since:2019-10-29 until:2019-11-02', 'NorCalFireList since:2019-11-02 until:2019-11-05', 'NorCalFireList since:2019-11-05 until:2019-11-09', 'NorCalFireList since:2019-11-09 until:2019-11-12', 'NorCalFireList since:2019-11-12 until:2019-11-16', 'NorCalFireList since:2019-11-16 until:2019-11-19', 'NorCalFireList since:2019-11-19 until:2019-11-23', 'NorCalFireList since:2019-11-23 until:2019-11-26', 'NorCalFireList since:2019-11-26 until:2019-11-29', 'NorCalFireList since:2019-11-29 until:2019-12-03', 'NorCalFireList since:2019-12-03 until:2019-12-06', 'NorCalFireList since:2019-12-06 until:2019-12-10', 'NorCalFireList since:2019-12-10 until:2019-12-13', 'NorCalFireList since:2019-12-13 until:2019-12-17', 'NorCalFireList since:2019-12-17 until:2019-12-20', 'NorCalFireList since:2019-12-20 until:2019-12-24', 'NorCalFireList since:2019-12-24 until:2019-12-2

INFO: Retrying... (Attempts left: 50)
INFO: Retrying... (Attempts left: 50)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: Using proxy 47.56.108.182:8118
INFO: Retrying... (Attempts left: 50)
INFO: Retrying... (Attempts left: 50)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-27%20until%3A2019-12-31&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-24%20until%3A2019-12-27&l=english
INFO: Using proxy 47.56.108.182:8118
INFO: Using proxy 47.56.108.1

INFO: Using proxy 196.216.220.201:53281
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: Using proxy 47.56.108.182:8118
INFO: Using proxy 196.216.220.201:53281
INFO: Retrying... (Attempts left: 48)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 196.216.220.201:53281
INFO: Retrying... (Attempts left: 48)
INFO: Retrying... (Attempts left: 48)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-27%20until%3A2019-12-31&l=english
INFO: Using proxy 196.216.220.201:53281
INFO: Using proxy 196.216.220.201:53281
INFO: Retrying... (Attempts left: 48)
INFO: Scraping 

INFO: Retrying... (Attempts left: 46)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Using proxy 103.87.207.188:58444
INFO: Retrying... (Attempts left: 46)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Retrying... (Attempts left: 46)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Retrying... (Attempts left: 46)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-24%20until%3A2019-12-27&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Scraping tweets from https://twitter.com/i/search/t

INFO: Using proxy 196.216.220.201:53281
INFO: Twitter returned : 'has_more_items' 
INFO: Got 52 tweets for NorCalFireList%20since%3A2019-10-29%20until%3A2019-11-02.
INFO: Got 100 tweets (52 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKPVhd-n_iAWgoCmzaKB9v8gEjUAFQAlAFUAFQAA&q=NorCalFireList%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 196.216.220.201:53281
INFO: Retrying... (Attempts left: 43)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-23%20until%3A2019-11-26&l=english
INFO: Using proxy 203.202.254.206:61456
INFO: Retrying... (Attempts left: 43)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-27%20until%3A2019-12-31&l=english
INFO: Using proxy 203.202.254.206:61456
I

...

INFO: Using proxy 109.86.121.118:46333
INFO: Using proxy 109.86.121.118:46333
INFO: Retrying... (Attempts left: 12)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-09%20until%3A2019-11-12&l=english
INFO: Using proxy 109.86.121.118:46333
INFO: Retrying... (Attempts left: 12)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-27%20until%3A2019-12-31&l=english
INFO: Using proxy 109.86.121.118:46333
INFO: Retrying... (Attempts left: 12)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 109.86.121.118:46333
INFO: Retrying... (Attempts left: 12)
INFO: Retrying... (Attempts left: 12)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-29%20until%3A2019-12-03&l=english
INFO: Scraping twee

INFO: Using proxy 115.74.201.137:42108
INFO: Using proxy 195.138.82.198:40301
INFO: Retrying... (Attempts left: 9)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-23%20until%3A2019-11-26&l=english
INFO: Using proxy 195.138.82.198:40301
INFO: Retrying... (Attempts left: 10)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-24%20until%3A2019-12-27&l=english
INFO: Using proxy 115.74.201.137:42108
INFO: Retrying... (Attempts left: 10)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 115.74.201.137:42108
INFO: Retrying... (Attempts left: 9)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Using proxy 195.138.82.198:40301
INFO: Retrying... (A

INFO: Retrying... (Attempts left: 7)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-20%20until%3A2019-12-24&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 91.191.250.142:31059
INFO: Using proxy 91.191.250.142:31059
INFO: Retrying... (Attempts left: 7)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: Using proxy 91.191.250.142:31059
INFO: Retrying... (Attempts left: 7)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 91.191.250.142:31059
INFO: Retrying... (Attempts left: 6)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20s

INFO: Retrying... (Attempts left: 5)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 148.251.200.196:1080
INFO: Retrying... (Attempts left: 5)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Using proxy 125.209.116.234:39301
INFO: Using proxy 125.209.116.234:39301
INFO: Retrying... (Attempts left: 4)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-09%20until%3A2019-11-12&l=english
INFO: Using proxy 148.251.200.196:1080
INFO: Retrying... (Attempts left: 4)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 148.251.200.196:1080
INFO: Retrying... (Attempts left: 4)
INFO: Scraping tweets 

INFO: Using proxy 188.43.52.166:47362
INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-11-29%20until%3A2019-12-03&l=english
INFO: Using proxy 188.43.52.166:47362
INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 188.43.52.166:47362
INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-24%20until%3A2019-12-27&l=english
INFO: Using proxy 188.43.52.166:47362
INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=NorCalFireList%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Using proxy 188.43.52.166:47362
INFO: Retrying... (Attempts left: 1)
INFO: Scraping tweets from ht

In [15]:
tweets_NorCalFireList= pd.DataFrame(t.__dict__ for t in tweets_NorCalFireList)

In [16]:
tweets_NorCalFireList.to_csv('../Data/tweets_NorCalFireList.csv')

In [17]:
tweets_UpfrontKPRA = query_tweets('UpfrontKPRA', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['UpfrontKPRA since:2019-10-23 until:2019-10-26', 'UpfrontKPRA since:2019-10-26 until:2019-10-29', 'UpfrontKPRA since:2019-10-29 until:2019-11-02', 'UpfrontKPRA since:2019-11-02 until:2019-11-05', 'UpfrontKPRA since:2019-11-05 until:2019-11-09', 'UpfrontKPRA since:2019-11-09 until:2019-11-12', 'UpfrontKPRA since:2019-11-12 until:2019-11-16', 'UpfrontKPRA since:2019-11-16 until:2019-11-19', 'UpfrontKPRA since:2019-11-19 until:2019-11-23', 'UpfrontKPRA since:2019-11-23 until:2019-11-26', 'UpfrontKPRA since:2019-11-26 until:2019-11-29', 'UpfrontKPRA since:2019-11-29 until:2019-12-03', 'UpfrontKPRA since:2019-12-03 until:2019-12-06', 'UpfrontKPRA since:2019-12-06 until:2019-12-10', 'UpfrontKPRA since:2019-12-10 until:2019-12-13', 'UpfrontKPRA since:2019-12-13 until:2019-12-17', 'UpfrontKPRA since:2019-12-17 until:2019-12-20', 'UpfrontKPRA since:2019-12-20 until:2019-12-24', 'UpfrontKPRA since:2019-12-24 until:2019-12-27', 'UpfrontKPRA since:2019-12-27 until:2019-12-31']
INFO

INFO: Using proxy 47.56.108.182:8118
INFO: Using proxy 47.56.108.182:8118
INFO: Retrying... (Attempts left: 50)
INFO: Retrying... (Attempts left: 50)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-02%20until%3A2019-11-05&l=english
INFO: Using proxy 47.56.108.182:8118
INFO: Using proxy 47.56.108.182:8118
INFO: Retrying... (Attempts left: 50)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-23%20until%3A2019-11-26&l=english
INFO: Using proxy 47.56.108.182:8118
INFO: Retrying... (Attempts left: 50)
INFO: Retrying... (Attempts left: 50)
INFO: Retrying... (Attempts left: 50)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-09%20until%3A2019-11-12&l=english
INF

INFO: Using proxy 196.216.220.201:53281
INFO: Retrying... (Attempts left: 48)
INFO: Retrying... (Attempts left: 48)
INFO: Retrying... (Attempts left: 48)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-09%20until%3A2019-11-12&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-24%20until%3A2019-12-27&l=english
INFO: Using proxy 196.216.220.201:53281
INFO: Using proxy 196.216.220.201:53281
INFO: Using proxy 196.216.220.201:53281
INFO: Retrying... (Attempts left: 48)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 196.216.220.201:53281
INFO: Retrying... (Attempts left: 48)
INFO: Retrying... (Attempt

INFO: Using proxy 103.87.207.188:58444
INFO: Retrying... (Attempts left: 46)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Retrying... (Attempts left: 46)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Retrying... (Attempts left: 46)
INFO: Using proxy 103.87.207.188:58444
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-02%20until%3A2019-11-05&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Retrying... (Attempts left: 46)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: Using proxy 103.87.207.188:58444
INFO: Retrying... (Attempts left: 46)
INFO: Scraping tweets from http

INFO: Using proxy 89.250.149.114:60981
INFO: Retrying... (Attempts left: 44)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 89.250.149.114:60981
INFO: Retrying... (Attempts left: 44)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 89.250.149.114:60981
INFO: Retrying... (Attempts left: 44)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Using proxy 89.250.149.114:60981
INFO: Retrying... (Attempts left: 44)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-12%20until%3A2019-11-16&l=english
INFO: Using proxy 89.250.149.114:60981
INFO: Retrying... (Attempts left: 44)
INFO: Scraping tweets from http

...

INFO: Using proxy 195.138.82.198:40301
INFO: Retrying... (Attempts left: 10)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Retrying... (Attempts left: 9)
INFO: Using proxy 115.74.201.137:42108
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 195.138.82.198:40301
INFO: Retrying... (Attempts left: 9)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-27%20until%3A2019-12-31&l=english
INFO: Using proxy 195.138.82.198:40301
INFO: Retrying... (Attempts left: 9)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-29%20until%3A2019-12-03&l=english
INFO: Using proxy 195.138.82.198:40301
INFO: Retrying... (Attempts left: 8)
INFO: Scraping tweets from https://

INFO: Using proxy 154.73.109.84:53281
INFO: Retrying... (Attempts left: 7)
INFO: Retrying... (Attempts left: 7)
INFO: Retrying... (Attempts left: 7)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 91.191.250.142:31059
INFO: Using proxy 91.191.250.142:31059
INFO: Using proxy 91.191.250.142:31059
INFO: Retrying... (Attempts left: 8)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Using proxy 154.73.109.84:53281
INFO: Retrying... (Attempts left: 7)
INFO: Scraping tweets from https://twi

INFO: Retrying... (Attempts left: 5)
INFO: Using proxy 125.209.116.234:39301
INFO: Retrying... (Attempts left: 5)
INFO: Retrying... (Attempts left: 5)
INFO: Retrying... (Attempts left: 6)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-20%20until%3A2019-12-24&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-23%20until%3A2019-11-26&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-27%20until%3A2019-12-31&l=english
INFO: Using proxy 125.209.116.234:39301
INFO: Retrying... (Attempts left: 5)
INFO:

INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-02%20until%3A2019-11-05&l=english
INFO: Using proxy 148.251.200.196:1080
INFO: Using proxy 103.208.152.34:37841
INFO: Retrying... (Attempts left: 3)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Using proxy 103.208.152.34:37841
INFO: Retrying... (Attempts left: 4)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-03%20until%3A2019-12-06&l=english
INFO: Retrying... (Attempts left: 4)
INFO: Using proxy 148.251.200.196:1080
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 148.251.200.196:1080
INFO: Retrying... (Attempts left: 3)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=d

INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-03%20until%3A2019-12-06&l=english
INFO: Using proxy 188.43.52.166:47362
INFO: Using proxy 188.43.52.166:47362
INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 188.43.52.166:47362
INFO: Retrying... (Attempts left: 2)
INFO: Retrying... (Attempts left: 2)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=default&q=UpfrontKPRA%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Using proxy 188.43.52.166:47362
INFO: Using proxy 188.43.52.166:47362
INFO: Retrying... (Attempts left: 1)
INFO: Scraping tweets from https://twitter.com/search?f=tweets&vertical=defaul

In [18]:
tweets_UpfrontKPRA= pd.DataFrame(t.__dict__ for t in tweets_UpfrontKPRA)

In [19]:
tweets_UpfrontKPRA.to_csv('../Data/tweets_UpfrontKPRA.csv')

In [ ]:
 CAPublicHealth, KQED

In [20]:
tweets_CAPublicHealth = query_tweets('CAPublicHealth', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['CAPublicHealth since:2019-10-23 until:2019-10-26', 'CAPublicHealth since:2019-10-26 until:2019-10-29', 'CAPublicHealth since:2019-10-29 until:2019-11-02', 'CAPublicHealth since:2019-11-02 until:2019-11-05', 'CAPublicHealth since:2019-11-05 until:2019-11-09', 'CAPublicHealth since:2019-11-09 until:2019-11-12', 'CAPublicHealth since:2019-11-12 until:2019-11-16', 'CAPublicHealth since:2019-11-16 until:2019-11-19', 'CAPublicHealth since:2019-11-19 until:2019-11-23', 'CAPublicHealth since:2019-11-23 until:2019-11-26', 'CAPublicHealth since:2019-11-26 until:2019-11-29', 'CAPublicHealth since:2019-11-29 until:2019-12-03', 'CAPublicHealth since:2019-12-03 until:2019-12-06', 'CAPublicHealth since:2019-12-06 until:2019-12-10', 'CAPublicHealth since:2019-12-10 until:2019-12-13', 'CAPublicHealth since:2019-12-13 until:2019-12-17', 'CAPublicHealth since:2019-12-17 until:2019-12-20', 'CAPublicHealth since:2019-12-20 until:2019-12-24', 'CAPublicHealth since:2019-12-24 until:2019-12-2

INFO: Using proxy 47.56.108.182:8118
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKep_JiUkCEWgMC82b3i-ZEhEjUAFQAlAFUAFQAA&q=CAPublicHealth%20since%3A2019-11-09%20until%3A2019-11-12&l=english
INFO: Using proxy 103.209.64.19:6666
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1199272080413343744-1200100867048984577&q=CAPublicHealth%20since%3A2019-11-26%20until%3A2019-11-29&l=english
INFO: Using proxy 47.56.108.182:8118
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1192127102847291392-1192947497737564163&q=CAPublicHealth%20since%3A2019-11-05%20until%3A2

INFO: Using proxy 103.209.64.19:6666
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLWp6PTh-yAWgMCggbXAlvwgEjUAFQAlAFUAFQAA&q=CAPublicHealth%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Using proxy 103.209.64.19:6666
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwLSJ0s-QxCEWgIC28di7g8ghEjUAFQAlAFUAFQAA&q=CAPublicHealth%20since%3A2019-12-20%20until%3A2019-12-24&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaEwLrRjbm3ryEWgMCgudLT_bAhEjUAFQAlAFUAFQAA&q=CAPublicHealth%20since%3A2019-12-03%20until%3A2019-12-06&l=english

INFO: Using proxy 196.216.220.201:53281
INFO: Twitter returned : 'has_more_items' 
INFO: Got 52 tweets for CAPublicHealth%20since%3A2019-12-20%20until%3A2019-12-24.
INFO: Got 489 tweets (52 new).
INFO: Twitter returned : 'has_more_items' 
INFO: Got 52 tweets for CAPublicHealth%20since%3A2019-11-05%20until%3A2019-11-09.
INFO: Got 541 tweets (52 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgLWxkaPf-SAWgMCggbXAlvwgEjUAFQAlAFUAFQAA&q=CAPublicHealth%20since%3A2019-10-23%20until%3A2019-10-26&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKblpajtgiEWgoC71evYmIUhEjUAFQAlAFUAFQAA&q=CAPublicHealth%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 196.216.220.

In [23]:
tweets_CAPublicHealth= pd.DataFrame(t.__dict__ for t in tweets_CAPublicHealth)

In [24]:
tweets_CAPublicHealth.to_csv('../Data/tweets_CAPublicHealth.csv')

In [9]:
tweets_KQED= query_tweets('KQED', begindate=begin_date, enddate=end_date,
                     limit=limit, lang=lang)

INFO: queries: ['KQED since:2019-10-23 until:2019-10-26', 'KQED since:2019-10-26 until:2019-10-29', 'KQED since:2019-10-29 until:2019-11-02', 'KQED since:2019-11-02 until:2019-11-05', 'KQED since:2019-11-05 until:2019-11-09', 'KQED since:2019-11-09 until:2019-11-12', 'KQED since:2019-11-12 until:2019-11-16', 'KQED since:2019-11-16 until:2019-11-19', 'KQED since:2019-11-19 until:2019-11-23', 'KQED since:2019-11-23 until:2019-11-26', 'KQED since:2019-11-26 until:2019-11-29', 'KQED since:2019-11-29 until:2019-12-03', 'KQED since:2019-12-03 until:2019-12-06', 'KQED since:2019-12-06 until:2019-12-10', 'KQED since:2019-12-10 until:2019-12-13', 'KQED since:2019-12-13 until:2019-12-17', 'KQED since:2019-12-17 until:2019-12-20', 'KQED since:2019-12-20 until:2019-12-24', 'KQED since:2019-12-24 until:2019-12-27', 'KQED since:2019-12-27 until:2019-12-31']
INFO: Querying KQED since:2019-10-26 until:2019-10-29
INFO: Querying KQED since:2019-10-23 until:2019-10-26
INFO: Querying KQED since:2019-11-12

INFO: Using proxy 139.99.89.133:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1206718855365582848-1206725510429999104&q=KQED%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 139.99.89.133:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1205224565837881351-1205276038412095488&q=KQED%20since%3A2019-12-10%20until%3A2019-12-13&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=TWEET-1198017442649378816-1198028158395510785&q=KQED%20since%3A2019-11-19%20until%3A2019-11-23&l=english
INFO: Using proxy 139.99.89.133:8080
INFO: Using proxy 1

INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaIwLX5qf_4iCEWgMCj3dGUhIkhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-11-02%20until%3A2019-11-05&l=english
INFO: Using proxy 165.227.33.50:8080
INFO: Using proxy 165.227.33.50:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKbdzMuOjiEWgICm_cSDnY4hEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKalksCBhSEWgoCn6eSImYUhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-10-29%20until%3A2019-11-02&l=english
INFO: Using proxy 165.227.33.

INFO: Using proxy 34.76.12.26:80
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKa5xbzvmiEWgMCmxbCwjJshEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Using proxy 34.76.12.26:80
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwL7pwPTCsCEWgoC2kdqn_bAhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-03%20until%3A2019-12-06&l=english
INFO: Using proxy 167.71.213.19:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKO5xrDGyiEWgsC-1d-wgcwhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-24%20until%3A2019-12-27&l=english


INFO: Using proxy 64.227.14.30:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKKB_MfCtSEWgoC36YfNj7YhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-06%20until%3A2019-12-10&l=english
INFO: Using proxy 64.227.14.30:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaKgLXNxuvkxiEWhIC1hbmylMghEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-20%20until%3A2019-12-24&l=english
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKO18bjjoiEWgMCmlbj3jaQhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-11-23%20until%3A2019-11-26&l=english
INFO: Using proxy 64.227.14.30:

...

INFO: Using proxy 207.154.231.212:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKLR1uCa_CAWgoCnoc2UiIAhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-10-26%20until%3A2019-10-29&l=english
INFO: Using proxy 207.154.231.212:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKOJ8dCTrSEWgoC2kdqn_bAhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-03%20until%3A2019-12-06&l=english
INFO: Using proxy 139.59.61.229:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKfR5KaB-iAWgMC6ibHHmfwgEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-10-23%20until%3A2019-10-2

INFO: Using proxy 139.59.61.229:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwL6t8LCqwCEWgICjleWlgcMhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: Using proxy 209.97.177.59:8080
INFO: Twitter returned : 'has_more_items' 
INFO: Got 298 tweets for KQED%20since%3A2019-11-26%20until%3A2019-11-29.
INFO: Got 2889 tweets (298 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwL39w8DyviEWgICo6amdk78hEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 209.97.177.59:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&res

INFO: Using proxy 138.197.145.103:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCwL2ZgerFkyEWgICm2eWonpchEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-11-12%20until%3A2019-11-16&l=english
INFO: Using proxy 138.197.145.103:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKiBh_2flyEWgMCmxbCwjJshEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-11-16%20until%3A2019-11-19&l=english
INFO: Using proxy 138.197.145.103:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwLXBv9jwviEWgICo6amdk78hEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-13%20until%3A2019-12

INFO: Using proxy 91.206.210.54:46698
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaKwL3RpKv5vyEWgICjleWlgcMhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-17%20until%3A2019-12-20&l=english
INFO: Using proxy 103.120.19.62:80
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaCgLflmbD8vSEWgICo6amdk78hEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 103.120.19.62:80
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKO5yJeFnCEWgsCjweeQoKAhEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-11-19%20until%3A2019-11-23&l=eng

INFO: Using proxy 82.196.11.105:8080
INFO: Twitter returned : 'has_more_items' 
INFO: Got 459 tweets for KQED%20since%3A2019-11-19%20until%3A2019-11-23.
INFO: Got 5352 tweets (459 new).
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAwKPNga3hiSEWgICm_cSDnY4hEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-11-05%20until%3A2019-11-09&l=english
INFO: Using proxy 82.196.11.105:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&reset_error_state=false&src=typd&max_position=thGAVUV0VFVBaAgKf5t4uevCEWgICo6amdk78hEjUAFQAlAFUAFQAA&q=KQED%20since%3A2019-12-13%20until%3A2019-12-17&l=english
INFO: Using proxy 176.9.119.170:8080
INFO: Scraping tweets from https://twitter.com/i/search/timeline?f=tweets&vertical=default&include_available_features=1&include_entities=1&res

In [10]:
tweets_KQED= pd.DataFrame(t.__dict__ for t in tweets_KQED)

In [11]:
tweets_KQED.to_csv('../Data/tweets_KQED.csv')

In [13]:
tweets_KQED =pd.read_csv('../Data/tweets_KQED.csv')

In [ ]:
# RedCrossNorCal, CalFireNews, BCWildfireWkly, CountyofSonoma
# NorthBayNews, KQEDnews, NorCalFireList, UpfrontKPRA, CAPublicHealth, KQED

In [20]:
tweets_RedCrossNorCal =pd.read_csv('../Data/tweets_RedCrossNorCal.csv',)
tweets_CalFireNews =pd.read_csv('../Data/tweets_CalFireNews.csv')
tweets_BCWildfireWkly =pd.read_csv('../Data/BCWildfireWkly.csv')
tweets_CountyofSonoma =pd.read_csv('../Data/tweets_CountyofSonoma.csv')
tweets_NorthBayNews =pd.read_csv('../Data/tweets_NorthBayNews.csv')

tweets_KQEDnews =pd.read_csv('../Data/tweets_KQEDnews.csv')
tweets_NorCalFireList =pd.read_csv('../Data/tweets_NorCalFireList.csv')
tweets_UpfrontKPRA =pd.read_csv('../Data/tweets_UpfrontKPRA.csv')
tweets_CAPublicHealth =pd.read_csv('../Data/tweets_CAPublicHealth.csv')
tweets_KQED =pd.read_csv('../Data/tweets_KQED.csv')

In [ ]:
frames = [df1, df2, df3]

result = pd.concat(frames)

In [29]:
all = [tweets_RedCrossNorCal, tweets_CalFireNews, tweets_BCWildfireWkly, tweets_CountyofSonoma,
      tweets_NorthBayNews, tweets_KQEDnews, tweets_NorCalFireList,tweets_UpfrontKPRA,
      tweets_CAPublicHealth, tweets_KQED]

In [30]:
kincade_all_tweets = pd.concat(all)

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [42]:
tweets_CalFireNews.columns

Index(['Unnamed: 0', 'screen_name', 'username', 'user_id', 'tweet_id',
       'tweet_url', 'timestamp', 'timestamp_epochs', 'text', 'text_html',
       'links', 'hashtags', 'has_media', 'img_urls', 'video_url', 'likes',
       'retweets', 'replies', 'is_replied', 'is_reply_to', 'parent_tweet_id',
       'reply_to_users'],
      dtype='object')

In [39]:
kincade_all_tweets.columns

Index(['has_media', 'hashtags', 'img_urls', 'is_replied', 'is_reply_to',
       'likes', 'links', 'parent_tweet_id', 'replies', 'reply_to_users',
       'retweets', 'screen_name', 'text', 'text_html', 'timestamp',
       'timestamp_epochs', 'tweet_id', 'tweet_url', 'user_id', 'username',
       'video_url'],
      dtype='object')

In [34]:
del kincade_all_tweets['Unnamed: 0']

In [43]:
kincade_all_tweets.to_csv('../Data/kincade_all_tweets.csv')

In [48]:
tweets_RedCrossNorCal.head(60)

Unnamed: 0      screen_name                               username  \
0            0      HivemindRes                      Hivemind Research   
1            1    NewCommGlobal                         NewComm Global   
2            2      HivemindRes                      Hivemind Research   
3            3    NewCommGlobal                         NewComm Global   
4            4  RedCrossBloodCA    Red Cross Blood Services - #GiveNow   
5            5  RedCrossBloodCA    Red Cross Blood Services - #GiveNow   
6            6  MakeSence_or_no                             Make Sense   
7            7  MakeSence_or_no                             Make Sense   
8            8   RedCrossNorCal  Red Cross Northern California Coastal   
9            9   RedCrossNorCal  Red Cross Northern California Coastal   
10          10   AStineGiftPlan                              Art Stine   
11          11      fx_medeiros                      Portuguese Yankee   
12          12   RedCrossNorCal  Red Cross Northern California Coastal   
13          13   RedCrossNorCal  Red Cross Northern California Coastal   
14          14   AStineGiftPlan                              Art Stine   
15          15      fx_medeiros                      Portuguese Yankee   
16          16   RedCrossNorCal  Red Cross Northern California Coastal   
17          17   RedCrossNorCal  Red Cross Northern California Coastal   
18          18   RedCrossNorCal  Red Cross Northern California Coastal   
19          19     Ms_Skygazer2                            ms_skygazer   
20          20   RedCrossNorCal  Red Cross Northern California Coastal   
21          21   RedCrossNorCal  Red Cross Northern California Coastal   
22          22   RedCrossNorCal  Red Cross Northern California Coastal   
23          23     Ms_Skygazer2                            ms_skygazer   
24          24   RedCrossNorCal  Red Cross Northern California Coastal   
25          25   RedCrossNorCal  Red Cross Northern California Coastal   
26          26        nordicgeo                    Nordic Geospatial 🌍   
27          27   RedCrossNorCal  Red Cross Northern California Coastal   
28          28   RedCrossNorCal  Red Cross Northern California Coastal   
29          29        nordicgeo                    Nordic Geospatial 🌍   
30          30   RedCrossNorCal  Red Cross Northern California Coastal   
31          31  RedCrossBloodCA    Red Cross Blood Services - #GiveNow   
32          32  GeneratorSafety                       Generator Safety   
33          33   RedCrossNorCal  Red Cross Northern California Coastal   
34          34  RedCrossBloodCA    Red Cross Blood Services - #GiveNow   
35          35  GeneratorSafety                       Generator Safety   
36          36   RedCrossNorCal  Red Cross Northern California Coastal   
37          37   RedCrossNorCal  Red Cross Northern California Coastal   
38          38   RedCrossNorCal  Red Cross Northern California Coastal   
39          39   RedCrossNorCal  Red Cross Northern California Coastal   
40          40    auser72307407                     skepticgirl👀⭐️⭐️⭐️   
41          41           KF5FUZ                         Kevin C. McCoy   
42          42   RedCrossNorCal  Red Cross Northern California Coastal   
43          43   RedCrossNorCal  Red Cross Northern California Coastal   
44          44   RedCrossNorCal  Red Cross Northern California Coastal   
45          45    auser72307407                     skepticgirl👀⭐️⭐️⭐️   
46          46           KF5FUZ                         Kevin C. McCoy   
47          47   RedCrossNorCal  Red Cross Northern California Coastal   
48          48   RedCrossNorCal  Red Cross Northern California Coastal   
49          49   RedCrossNorCal  Red Cross Northern California Coastal   
50          50           KF5FUZ                         Kevin C. McCoy   
51          51   RedCrossNorCal  Red Cross Northern California Coastal   
52          52   RedCrossNorCal  Red Cross Northern California Coastal   
53      

## DATA CLEANING

In [8]:
pwd

'/Users/Brian 1/Desktop/GA_12.10_1.04/shelter_status/code'

In [11]:
kincade = pd.read_csv('../data/kincade_all_tweets.csv')

In [15]:
kincade.drop(columns='Unnamed: 0',axis = 1, inplace=True)

In [ ]:
df[df['A'].str.contains("hello")]

In [19]:
kincade[kincade['screen_name'].str.contains('RedCross')]

has_media                              hashtags  \
4          False                     ['BeTheLifeline']   
5          False                     ['BeTheLifeline']   
8           True  ['GiveWithMeaning', 'GivingTuesday']   
9           True                   ['EndHomeFirespic']   
12          True  ['GiveWithMeaning', 'GivingTuesday']   
...          ...                                   ...   
754         True                    ['KincadeFirepic']   
6938       False                                    []   
16497       True                                    []   
16498       True                    ['KincadeFirepic']   
16526      False                       ['kincadefire']   

                                                img_urls  is_replied  \
4                                                     []       False   
5                                                     []       False   
8      ['https://pbs.twimg.com/media/EK0GBieUwAE3l9_....       False   
9      ['https://pbs.twimg.com/media/EKztvTPWsAEmuaG....       False   
12     ['https://pbs.twimg.com/media/EK0GBieUwAE3l9_....       False   
...                                                  ...         ...   
754    ['https://pbs.twimg.com/media/EHxClDRU4AA-e_r....       False   
6938                                                  []       False   
16497  ['https://pbs.twimg.com/media/EIJEXV1X0AEMr2k....       False   
16498  ['https://pbs.twimg.com/media/EIJEXV1X0AEMr2k....        True   
16526                                                 []        True   

       is_reply_to  likes                                              links  \
4            False    3.0  ['https://twitter.com/DublinPIO/status/1204106...   
5            False    3.0  ['https://twitter.com/DublinPIO/status/1204106...   
8            False    4.0                       ['http://redcross.org/gift']   
9            False   11.0                                                 []   
12           False    4.0                       ['http://redcross.org/gift']   
...            ...    ...                                                ...   
754          False   33.0                                                 []   
6938          True    0.0              ['http://www.redcross.org/volunteer']   
16497        False    0.0                                                 []   
16498        False   77.0                     ['https://rdcrss.org/31SZ9Fm']   
16526        False   30.0  ['https://twitter.com/KQED/status/118935500018...   

       parent_tweet_id  replies  \
4                  NaN      0.0   
5                  NaN      0.0   
8                  NaN      0.0   
9                  NaN      0.0   
12                 NaN      0.0   
...                ...      ...   
754                NaN      0.0   
6938      1.188668e+18      0.0   
16497              NaN      0.0   
16498              NaN      1.0   
16526              NaN      1.0   

                                          reply_to_users  retweets  \
4                                                     []       1.0   
5                                                     []       1.0   
8                                                     []       0.0   
9                                                     []       2.0   
12                                                    []       0.0   
...                                                  ...       ...   
754                                                   []      41.0   
6938   [{'screen_name': 'WCKitchen', 'user_id': '1566...       0.0   
16497                                                 []       0.0   
16498                                                 []      38.0   
16526                                                 []       9.0   

           screen_name                                               text  \
4      RedCrossBloodCA  City of Dublin, @DublinPIO, thank you for host...   
5      RedCrossBloodCA  City of Dublin, @DublinPIO, thank you for ho